In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
!nvidia-smi

Tue Feb 26 22:35:20 2019       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 384.130                Driver Version: 384.130                   |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  GeForce GTX 108...  Off  | 00000000:05:00.0 Off |                  N/A |
| 24%   44C    P8    17W / 250W |    165MiB / 11170MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
|   1  GeForce GTX 108...  Off  | 00000000:06:00.0 Off |                  N/A |
| 23%   43C    P8    17W / 250W |     10MiB / 11172MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
|   2  G

In [3]:
import os
os.environ['CUDA_VISIBLE_DEVICES'] = "3"

# 1 - Dataset creation

CSV

In [4]:
import os
import glob
import pandas as pd

In [5]:
# dataset_path = '/root/data/rnd/small_pen_data_collection/sotra-small-pen/pen-1/2018-10-01/'

In [6]:
# base_dir = '/root/data/rnd/small_pen_data_collection/sotra-small-pen/pen-1/2018-10-01/'
# experiences = os.listdir(base_dir)
# all_image_path = []
# for experience in experiences:
#     folder_path = os.path.join(base_dir, experience)
#     if not os.path.isdir(folder_path):
#         continue
#     if "rectified" not in folder_path:
#         continue
#     if "reference" in folder_path:
#         continue
#     print(folder_path)
#     all_image_path += glob.glob(folder_path + '/*.jpg')

In [7]:
# all_image_path = glob.glob('/root/data/depthmap/*.jpg')
# all_image_path = sorted(all_image_path, key = lambda k:int(os.path.basename(k).split('.')[0].split('_')[-1]))

In [8]:
# all_image_path = []
# with open('/root/thomas/github/cv_research/thomas/full_pipeline/small_pen/to_forwardpass.txt', 'r') as f:
#     for line in f:
#         all_image_path.append(line[:-1])
# all_image_path = sorted(all_image_path)

In [9]:
all_image_path = glob.glob("/root/data/lice-data/crops/blom-kjeppevikholmen/*/2/*.jpg")

In [10]:
dataframe = pd.DataFrame(all_image_path[:], columns=['image path'])
dataframe.head()

image path
0  /root/data/lice-data/crops/blom-kjeppevikholme...
1  /root/data/lice-data/crops/blom-kjeppevikholme...
2  /root/data/lice-data/crops/blom-kjeppevikholme...
3  /root/data/lice-data/crops/blom-kjeppevikholme...
4  /root/data/lice-data/crops/blom-kjeppevikholme...

Data Loader

In [11]:
from torch.utils.data import Dataset
import numpy as np
import pandas as pd
from PIL import Image
import skimage

In [12]:
class DataGenerator(Dataset):
    """
    Load a dataset for target estimation
    
    Args:
       - dataframe: DataFrame of image path
    """
    def __init__(self, dataframe):
        self.dataframe = dataframe
    
    def __getitem__(self, index):
        img_path = self.dataframe.iloc[:, 0][index]
        img = skimage.io.imread(img_path)
        
        return img, img_path
    
    def __len__(self):
        return len(self.dataframe)

In [13]:
data_generator = DataGenerator(dataframe)

# 2 - MaskRCNN forward pass

### 2.1 - Load the model

In [14]:
import os
import sys
import random
import math
import re
import time
import numpy as np
import cv2
import matplotlib
import matplotlib.pyplot as plt
import keras

sys.path.insert(0, '../libraries')
from mrcnn.config import Config
import mrcnn.utils as utils
import mrcnn.model as modellib
import mrcnn.visualize as visualize
from mrcnn.model import log
import mcoco.coco as coco
# import mextra.utils as extra_utils
from PIL import ImageFile
ImageFile.LOAD_TRUNCATED_IMAGES = True

%matplotlib inline
%config IPCompleter.greedy=True
BASE_DIR = '/root/data/models/erko/mask_rcnn_instance_segmentation'
DATA_DIR = '/root/data/erko/'
WEIGHTS_DIR = os.path.join(BASE_DIR, "weights")
MODEL_DIR = os.path.join(BASE_DIR, "logs")

# Local path to trained weights file
COCO_MODEL_PATH = os.path.join(WEIGHTS_DIR, "mask_rcnn_coco.h5")
# Download COCO trained weights from Releases if needed
if not os.path.exists(COCO_MODEL_PATH):
    utils.download_trained_weights(COCO_MODEL_PATH)

Using TensorFlow backend.
/usr/local/lib/python3.5/dist-packages/pycocotools/coco.py:49: UserWarning: 
This call to matplotlib.use() has no effect because the backend has already
been chosen; matplotlib.use() must be called *before* pylab, matplotlib.pyplot,
or matplotlib.backends is imported for the first time.

The backend was *originally* set to 'module://ipykernel.pylab.backend_inline' by the following code:
  File "/usr/lib/python3.5/runpy.py", line 184, in _run_module_as_main
    "__main__", mod_spec)
  File "/usr/lib/python3.5/runpy.py", line 85, in _run_code
    exec(code, run_globals)
  File "/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py", line 16, in <module>
    app.launch_new_instance()
  File "/usr/local/lib/python3.5/dist-packages/traitlets/config/application.py", line 658, in launch_instance
    app.start()
  File "/usr/local/lib/python3.5/dist-packages/ipykernel/kernelapp.py", line 486, in start
    self.io_loop.start()
  File "/usr/local/lib/python3.5/di

In [15]:
def get_ax(rows=1, cols=1, size=8):
    """Return a Matplotlib Axes array to be used in
    all visualizations in the notebook. Provide a
    central point to control graph sizes.
    
    Change the default size attribute to control the size
    of rendered images
    """
    _, ax = plt.subplots(rows, cols, figsize=(size*cols, size*rows))
    return ax

In [16]:
image_size = 1024
rpn_anchor_template = (1, 2, 4, 8, 16) # anchor sizes in pixels
rpn_anchor_scales = tuple(i * (image_size // 16) for i in rpn_anchor_template)

class FishConfig(Config):
    """Configuration for training on the shapes dataset.
    """
    # name your experiments here
    NAME = "full"

    # Train on 1 GPU and 2 images per GPU. Put multiple images on each
    # GPU if the images are small. Batch size is 2 (GPUs * images/GPU).
    GPU_COUNT = 1
    IMAGES_PER_GPU = 2

    # Number of classes (including background)
    NUM_CLASSES = 9 + 1  # background + 3 shapes (triangles, circles, and squares)

    # Use smaller images for faster training. 
    IMAGE_MAX_DIM = image_size
    IMAGE_MIN_DIM = image_size
    
    # Use smaller anchors because our image and objects are small
    RPN_ANCHOR_SCALES = rpn_anchor_scales

    # Aim to allow ROI sampling to pick 33% positive ROIs.
    TRAIN_ROIS_PER_IMAGE = 32

    STEPS_PER_EPOCH = 1000

    VALIDATION_STEPS = 300
    
config = FishConfig()
config.display()


Configurations:
BACKBONE                       resnet101
BACKBONE_STRIDES               [4, 8, 16, 32, 64]
BATCH_SIZE                     2
BBOX_STD_DEV                   [0.1 0.1 0.2 0.2]
COORDCONV                      False
DETECTION_MAX_INSTANCES        100
DETECTION_MIN_CONFIDENCE       0.7
DETECTION_NMS_THRESHOLD        0.3
GPU_COUNT                      1
GRADIENT_CLIP_NORM             5.0
IMAGES_PER_GPU                 2
IMAGE_MAX_DIM                  1024
IMAGE_META_SIZE                22
IMAGE_MIN_DIM                  1024
IMAGE_MIN_SCALE                0
IMAGE_RESIZE_MODE              square
IMAGE_SHAPE                    [1024 1024    3]
LEARNING_MOMENTUM              0.9
LEARNING_RATE                  0.001
LOSS_WEIGHTS                   {'mrcnn_class_loss': 1.0, 'mrcnn_bbox_loss': 1.0, 'rpn_bbox_loss': 1.0, 'rpn_class_loss': 1.0, 'mrcnn_mask_loss': 1.0}
MASK_POOL_SIZE                 14
MASK_SHAPE                     [28, 28]
MAX_GT_INSTANCES               100
MEAN_PIXEL 

In [17]:
# model = modellib.MaskRCNN(mode="training", config=config, model_dir=MODEL_DIR)

In [18]:
# model_path = '/root/data/models/small_pen/body_parts/logs/body_parts_uncomlpete_1024_20181010_21H08/mask_rcnn_body_parts_uncomlpete_1024_0100.h5'
model_path = '/root/data/models/erko/mask_rcnn_instance_segmentation/logs/body_part_segmentation_20181031_21H02/mask_rcnn_body_part_segmentation_0100.h5'

In [19]:
class InferenceConfig(FishConfig):
    GPU_COUNT = 1
    IMAGES_PER_GPU = 1

inference_config = InferenceConfig()

# Recreate the model in inference mode
model = modellib.MaskRCNN(mode="inference", 
                          config=inference_config,
                          model_dir=MODEL_DIR)

# Get path to saved weights
# Either set a specific path or find last trained weights
# model_path = os.path.join(ROOT_DIR, ".h5 file name here")
model.find_last()[1]

# Load trained weights (fill in path to trained weights here)
assert model_path != "", "Provide path to trained weights"

# model_path = '/root/data/models/erko/mask_rcnn_instance_segmentation/logs/full_20181002_19H09/mask_rcnn_full_0097.h5'
print("Loading weights from ", model_path)
model.load_weights(model_path, by_name=True)

Tensor("input_rpn_feature_map:0", shape=(?, ?, ?, 256), dtype=float32)
Loading weights from  /root/data/models/erko/mask_rcnn_instance_segmentation/logs/body_part_segmentation_20181031_21H02/mask_rcnn_body_part_segmentation_0100.h5


In [20]:
# import time

In [21]:
original_image, img_path = data_generator[0]

In [22]:
# speed = []
# for i in range(1, 10):
#     class InferenceConfig(FishConfig):
#         GPU_COUNT = 1
#         print(i)
#         IMAGES_PER_GPU = i

#     inference_config = InferenceConfig()

#     # Recreate the model in inference mode
#     model = modellib.MaskRCNN(mode="inference", 
#                               config=inference_config,
#                               model_dir=MODEL_DIR)

#     # Get path to saved weights
#     # Either set a specific path or find last trained weights
#     # model_path = os.path.join(ROOT_DIR, ".h5 file name here")
#     model.find_last()[1]

#     # Load trained weights (fill in path to trained weights here)
#     assert model_path != "", "Provide path to trained weights"

#     # model_path = '/root/data/models/erko/mask_rcnn_instance_segmentation/logs/full_20181002_19H09/mask_rcnn_full_0097.h5'
#     print("Loading weights from ", model_path)
#     model.load_weights(model_path, by_name=True)

#     start = time.time()
#     results = model.detect([original_image]*i, verbose=1)
#     end = time.time()
#     speed.append(end - start)
    

In [23]:
# linear = [k*speed[0] for k in range(1, 10)]

In [24]:
# plt.plot(range(1, 10), linear)
# plt.plot(range(1, 10), speed)
# plt.legend(['ohne batch', 'mit batch'])

### 2.2 - Visualize results

In [26]:
# try:
#     while True:
#         for image_id in range(len(data_generator)):
#             original_image, _ = data_generator[image_id]
#             results = model.detect([original_image], verbose=1)
#             r = results[0]
#             visualize.display_instances(original_image, r['rois'], r['masks'], r['class_ids'], 
#                             ['BG', 'salmon'], r['scores'], ax=get_ax())

#             input('Press enter to continue: ')
# except KeyboardInterrupt:
#     pass

### 2.3 - Save coco file

In [27]:
import json
import pylab
import matplotlib.pyplot as plt
from tempfile import NamedTemporaryFile
from pycocotools.coco import COCO
# from mextra.utils import result_to_coco
from cococreatortools import * 
from datetime import datetime

In [28]:
from tqdm import tqdm

In [29]:
INFO = {
    "description": "Fish data",
    "url": "https://github.com/waspinator/pycococreator",
    "version": "0.1.0",
    "year": 2018,
    "contributor": "thossler",
    "date_created": datetime.utcnow().isoformat(' ')
}

LICENSES = [
    {
        "id": 1,
        "name": "Attribution-NonCommercial-ShareAlike License",
        "url": "http://creativecommons.org/licenses/by-nc-sa/2.0/"
    }
]

CATEGORIES = [
{1: {'id': 1, 'name': 'F', 'supercategory': 'F'},
 2: {'id': 2, 'name': 'Freckles', 'supercategory': 'Freckles'},
 3: {'id': 3, 'name': 'Head', 'supercategory': 'Head'},
 4: {'id': 4, 'name': 'Dorsal Fin', 'supercategory': 'Dorsal Fin'},
 5: {'id': 5, 'name': 'Adipose Fin', 'supercategory': 'Adipose Fin'},
 6: {'id': 6, 'name': 'Anal Fin', 'supercategory': 'Anal Fin'},
 7: {'id': 7, 'name': 'Pelvic Fin', 'supercategory': 'Pelvic Fin'},
 8: {'id': 8, 'name': 'Pectoral Fin', 'supercategory': 'Pectoral Fin'},
 9: {'id': 9, 'name': 'Eye', 'supercategory': 'Eye'},
 10: {'id': 10, 'name': 'Caudal Fin', 'supercategory': 'Caudal Fin'}}
]

In [30]:
coco_output = {"info": INFO, "licenses": LICENSES, "categories": CATEGORIES, "images": [], "annotations": []}

In [31]:
# len(data_generator)
segmentation_id = 1

In [32]:
for image_id in tqdm(range(len(data_generator))):
    original_image, img_path = data_generator[image_id]
    height,width,_ = original_image.shape
    print(img_path)
    if original_image is not None:
        print(image_id)
        
        results = model.detect([original_image], verbose=1)[0]

        # create the coco stuff
        image_info = create_image_info(image_id, img_path, [width, height])
        coco_output['images'].append(image_info)

        # loop through all the fish detected
        detections_number = len(results['class_ids'])
        for k in range(detections_number):
            # print(segmentation_id)
            category_info = {'id': int(results['class_ids'][k])}
            binary_mask = results['masks'][..., k]
            annotation_info = create_annotation_info(segmentation_id, image_id, category_info, binary_mask,
                                                     [width, height], bounding_box=results['rois'][k, ...], tolerance=2)
            if annotation_info is not None:
                coco_output["annotations"].append(annotation_info)
            segmentation_id += 1


  0%|          | 0/5844 [00:00<?, ?it/s]

/root/data/lice-data/crops/blom-kjeppevikholmen/2018-12-25/2/left_blom-kjeppevikholmen_2_1545741072768_1_838_3067_2387.jpg
0
Processing 1 images
image                    shape: (1549, 3066, 3)       min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  136.20000  float64
image_metas              shape: (1, 22)               min:    0.00000  max: 3066.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.70780  max:    1.64524  float32


  0%|          | 1/5844 [00:01<2:49:56,  1.75s/it]

/root/data/lice-data/crops/blom-kjeppevikholmen/2018-12-25/2/left_blom-kjeppevikholmen_2_1545732229819_919_70_4096_1647.jpg
1
Processing 1 images
image                    shape: (1577, 3177, 3)       min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 22)               min:    0.00000  max: 3177.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.70780  max:    1.64524  float32


  0%|          | 2/5844 [00:03<2:39:03,  1.63s/it]

...

100%|█████████▉| 5842/5844 [1:35:10<00:01,  1.02it/s]

/root/data/lice-data/crops/blom-kjeppevikholmen/2018-12-19/2/left_blom-kjeppevikholmen_2_1545216741367_0_577_2493_2004.jpg
5842
Processing 1 images
image                    shape: (1427, 2493, 3)       min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 22)               min:    0.00000  max: 2493.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.70780  max:    1.64524  float32


100%|█████████▉| 5843/5844 [1:35:11<00:00,  1.02it/s]

/root/data/lice-data/crops/blom-kjeppevikholmen/2018-12-19/2/left_blom-kjeppevikholmen_2_1545228214622_0_0_4096_2534.jpg
5843
Processing 1 images
image                    shape: (2534, 4096, 3)       min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  138.20000  float64
image_metas              shape: (1, 22)               min:    0.00000  max: 4096.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.70780  max:    1.64524  float32


100%|██████████| 5844/5844 [1:35:13<00:00,  1.02it/s]


In [34]:
with open('/root/data/lice-data/crops/blom-kjeppevikholmen-results.json', 'w') as f:
    json.dump(coco_output, f)